# Documentación del Notebook: Predicción de Coeficientes de Zernike a partir de Imágenes Hartmann-Shack para ResNet18 por defecto de pythorch

Este notebook implementa un pipeline completo para entrenar y evaluar un modelo de `Deep Learning` (basado en ResNet-18) capaz de predecir 20 coeficientes de Zernike a partir de imágenes simuladas de un sensor Hartmann-Shack. El proceso incluye la instalación de dependencias, descarga y preparación del dataset, definición del modelo, entrenamiento, evaluación y visualización de resultados.

## Descripción del Proceso de Generación de Imágenes

Este documento describe el proceso utilizado para generar el dataset de imágenes, centrándose en la simulación de aberraciones ópticas mediante Coeficientes de Zernike y su representación a través del método de Hartmann-Shack.

### 1. Coeficientes de Zernike

Los Coeficientes de Zernike son una serie de polinomios ortogonales utilizados comúnmente en óptica para describir las aberraciones de un frente de onda. En este dataset, cada imagen es generada a partir de un conjunto de **20 coeficientes de Zernike**.

*   **Número de Coeficientes:** Se utilizan los primeros 20 coeficientes de Zernike (excluyendo el pistón, que solo representa un cambio de fase global y no afecta la forma de la imagen).
*   **Rango de Valores:** Cada uno de estos 20 coeficientes de Zernike varía dentro de un rango de **-8 a 8 micrometros**.
    *   Este rango permite simular una amplia variedad de aberraciones, desde las más comunes (como el desenfoque y el astigmatismo) hasta las de orden superior, capturando la complejidad de los frentes de onda que se encuentran en sistemas ópticos reales o en el ojo humano.
    *   La variabilidad de los coeficientes asegura una diversidad en el dataset, crucial para entrenar modelos robustos de aprendizaje automático.

### 2. Método de Simulación Hartmann-Shack

La generación de las imágenes se realiza mediante la simulación de un **sensor de frente de onda Hartmann-Shack**. Este método es fundamental para la caracterización de las aberraciones:

*   **Principio:** Un sensor Hartmann-Shack consiste en una matriz de microlentes que dividen el frente de onda incidente en múltiples pequeños sub-aperturas. Cada microlente enfoca la luz en un punto en un detector (por ejemplo, un CCD).
*   **Detección de Aberraciones:** Si el frente de onda es plano y perfecto, todos los puntos focales de las microlentes formarán una cuadrícula regular. Sin embargo, en presencia de aberraciones, los puntos focales se desplazan de sus posiciones ideales. La magnitud y dirección de estos desplazamientos son directamente proporcionales a la pendiente local del frente de onda.
*   **Generación de Imágenes:** En esta simulación, los 20 coeficientes de Zernike definen un frente de onda aberrado. Este frente de onda es entonces "medido" virtualmente por un sensor Hartmann-Shack simulado. La salida de esta simulación es una imagen que representa los desplazamientos de los spots focales, que es la imagen que compone el dataset.

### Resumen del Proceso

1.  Se seleccionan aleatoriamente 20 coeficientes de Zernike, cada uno dentro del rango [-1, 1].

2. Los coeficientes 1 y 2 varian entre -17 y 17 micrómetros generados aleatoriamente, el coeficiente 0 no se toma puesto que no aporta información relevante.
3.  Estos coeficientes definen un frente de onda con aberraciones específicas.
4.  Se simula cómo un sensor Hartmann-Shack "vería" 4ste frente de onda aberrado.
5.  La salida de esta simulación (la imagen de los spots desplazados) se guarda como una entrada en el dataset.

Este enfoque permite crear un dataset diverso y representativo de frentes de onda con aberraciones conocidas y también se crea una cantida de imágines específica para garantizar un rango dinámico amplo para ser evaluado, lo que es ideal para entrenar y evaluar modelos capaces de predecir o clasificar aberraciones ópticas a partir de imágenes de Hartmann-Shack.

### Instalación de Librerías

Este bloque de código se encarga de instalar todas las librerías necesarias para el proyecto. Utiliza `pip install --quiet` para una instalación silenciosa de paquetes como `numpy`, `pandas`, `pillow`, `matplotlib`, `tqdm`, `scipy` (para correlación de Pearson), `scikit-learn` (para MAE, R2), `plotly` (para gráficas interactivas) y las dependencias de `PyTorch` (`torch`, `torchvision`, `torchaudio`) compatibles con CUDA. También instala `gdown` para la descarga desde Google Drive. Al finalizar, imprime un mensaje de confirmación.

## 1. Configuración del Entorno

Esta sección se encarga de preparar el entorno de ejecución, instalando todas las librerías necesarias para el desarrollo y la ejecución del modelo.

In [ ]:
# ============================================================
# 🔧 Instalación de todas las librerías necesarias (Colab)
# ============================================================

# Básicos
!pip install --quiet numpy pandas pillow matplotlib tqdm numpy

# SciPy (para correlación Pearson)
!pip install --quiet scipy

# Scikit-Learn (MAE, R2)
!pip install --quiet scikit-learn

# Plotly (gráficas interactivas)
!pip install --quiet plotly

# PyTorch + TorchVision compatible con CUDA (Colab)
# Colab ya incluye PyTorch, pero forzamos actualización estable.
!pip install --quiet torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu118

!pip install gdown
print("Todas las dependencias han sido instaladas correctamente.")


## 2. Importación de Librerías

Este bloque importa todas las librerías y módulos que se utilizarán a lo largo del notebook. Incluye módulos para:
- **Manejo de archivos y rutas**: `os`, `zipfile`, `gdown`, `re`.
- **Manipulación de datos numéricos y estructuras**: `numpy` (como `np`), `PIL` (como `Image`), `pandas` (como `pd`), `random`.
- **Estadísticas y métricas**: `scipy.stats` (para correlación de Pearson), `sklearn.metrics` (para MAE, R2).
- **PyTorch**: `torch`, `torch.nn`, `torch.nn.functional` (como `F`), `torch.optim`, `torch.utils.data` (`Dataset`, `DataLoader`).
- **Procesamiento de imágenes**: `torchvision.transforms` (como `transforms`), `torchvision.transforms.ToPILImage`, `torchvision.models.feature_extraction.create_feature_extractor`.
- **Visualización**: `tqdm` (para barras de progreso), `matplotlib.pyplot` (como `plt`), `plotly.express` (como `px`), `plotly.graph_objects` (como `go`), `plotly.subplots.make_subplots`.

In [ ]:
import os
import zipfile
import gdown
import re

import numpy as np
from PIL import Image
import pandas as pd
import random


import scipy.stats as stats  # Para calcular la correlación de Pearson
from sklearn.metrics import mean_absolute_error, r2_score

import torch
import torch.nn as nn
import torch.nn.functional as F

import torch.optim as optim
from torch.utils.data import Dataset, DataLoader

import torchvision.transforms as transforms
from torchvision.transforms import ToPILImage
from torchvision.models.feature_extraction import create_feature_extractor
from torchvision.models import resnet18, ResNet18_Weights

from tqdm import tqdm  # Para mostrar el progreso

import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

## 3. Descarga y Preparación del Dataset

Esta sección maneja la adquisición y descompresión de los datos, así como la verificación de la estructura de archivos. El dataset contiene imágenes de Hartmann-Shack y sus correspondientes coeficientes de Zernike.

### 3.1 Descarga de Datos desde Google Drive

Este bloque define un `folder_id` de Google Drive y construye una URL para la descarga. Luego, utiliza la librería `gdown` para descargar la carpeta completa especificada por la URL. La descarga se guarda en el directorio `./data` dentro del entorno de Colab. Al finalizar, muestra un mensaje de confirmación de la descarga.

In [ ]:
folder_id = "14--HWvqgHGtH5TVJu3sqSGAp2tEYTsYi"
url = f"https://drive.google.com/drive/folders/{folder_id}"

print("Descargando carpeta desde Google Drive...")
gdown.download_folder(url, output="./data", remaining_ok=True)

print("✔️ Descarga completa. Los archivos están en ./data")

Descargando carpeta desde Google Drive...


Retrieving folder contents


Processing file 1a65zvPWX61PEHfdEwhU9OU3Aqq_NLLf1 archive.zip


Retrieving folder contents completed
Building directory structure
Building directory structure completed
Downloading...
From (original): https://drive.google.com/uc?id=1a65zvPWX61PEHfdEwhU9OU3Aqq_NLLf1
From (redirected): https://drive.google.com/uc?id=1a65zvPWX61PEHfdEwhU9OU3Aqq_NLLf1&confirm=t&uuid=54d6dcc5-dd8d-4e5f-a033-890c9c6a336d
To: /content/data/archive.zip
100%|██████████| 743M/743M [00:07<00:00, 100MB/s]

✔️ Descarga completa. Los archivos están en ./data



Download completed


### 3.2 Descompresión del Dataset

Este bloque de código se encarga de descomprimir el archivo `archive.zip` descargado en la etapa anterior. Primero, verifica si el archivo `archive.zip` existe en la ruta especificada (`./data/archive.zip`). Si no lo encuentra, lanza un error. Luego, utiliza la librería `zipfile` para extraer todo el contenido del archivo zip en el directorio `./data`. Al finalizar, imprime un mensaje de confirmación de que la descompresión fue exitosa.

In [ ]:
zip_path = "./data/archive.zip"
extract_to = "./data"

# Verificar si existe
if not os.path.exists(zip_path):
    raise FileNotFoundError(f"No se encontró el archivo: {zip_path}")

print("Descomprimiendo dataset (esto puede tardar)...")

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(extract_to)

print("Listo ✔️")


Descomprimiendo dataset (esto puede tardar)...
Listo ✔️


### 3.3 Verificación de la Estructura de Directorios

Este bloque de código simple recorre el directorio `./content/data` y sus subdirectorios utilizando `os.walk`. Su propósito es imprimir la estructura de directorios, lo cual es útil para verificar que los archivos se hayan descargado y descomprimido correctamente y para entender la organización de los datos.

In [ ]:
for root, _, _ in os.walk("./data", topdown=True):
    print(root)

/content/data
/content/data/DataSet_Zernike_20_Coef
/content/data/DataSet_Zernike_20_Coef/Train
/content/data/DataSet_Zernike_20_Coef/Validation
/content/data/DataSet_Zernike_20_Coef/Test


## 4. Configuración del Dataset y DataLoader

Esta sección define cómo se cargarán y preprocesarán las imágenes y sus coeficientes asociados para el entrenamiento y la validación del modelo. Se verifica la disponibilidad de GPU y se define una clase personalizada para el dataset.

### 4.1 Clase `CombinedDataset`

La clase `CombinedDataset` hereda de `torch.utils.data.Dataset` y se encarga de:
- Cargar imágenes PNG y sus respectivos archivos de texto de coeficientes.
- Aplicar transformaciones a las imágenes (redimensionamiento, conversión a tensor).
- Asegurar que cada imagen tenga un archivo de coeficientes asociado.
- Mezclar aleatoriamente los datos.

La función `is_valid_number` es una utilidad para verificar la validez de los números en los archivos de coeficientes.

In [ ]:
# Verificar si GPU está disponible y configurar dispositivo
# Configuración general
torch.backends.cudnn.benchmark = True
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Clase para cargar imágenes desde múltiples directorios
class CombinedDataset(Dataset):
    def __init__(self, directories, transform=None):
        self.transform = transform
        self.samples = []

        # Recorrer cada directorio y almacenar archivos en una lista
        for image_dir in directories:
            filenames = [f for f in os.listdir(image_dir) if f.endswith('.png')]
            for filename in filenames:
                img_path = os.path.join(image_dir, filename)
                coef_path = os.path.join(image_dir, f'coef_{filename[4:-4]}.txt')
                if os.path.exists(coef_path):  # Asegurar que existe el archivo de coeficientes
                    self.samples.append((img_path, coef_path))

        # Mezclar aleatoriamente los datos combinados
        random.shuffle(self.samples)

    def __len__(self):
        return len(self.samples)

    def __getitem__(self, idx):
        img_path, coef_path = self.samples[idx]

        # Cargar imagen
        image = Image.open(img_path).convert('L')

        if self.transform:
            image = self.transform(image)

        # Leer coeficientes línea por línea
        with open(coef_path, 'r') as f:
            lines = f.readlines()
            coefficients = [float(x.strip()) for x in lines if is_valid_number(x.strip())]

        if len(coefficients) == 0:
            raise ValueError(f"Archivo sin coeficientes válidos: {coef_path}")

        coefficients = torch.tensor(coefficients, dtype=torch.float32)

        return image, coefficients

def is_valid_number(s):
    """ Verifica si 's' es un número válido, incluyendo notación científica. """
    try:
        float(s)  # Intenta convertir a float
        return True
    except ValueError:
        return False



### 4.2 Transformaciones y Configuración de DataLoaders

Se definen las transformaciones de imagen (redimensionamiento y conversión a tensor) y se configuran los `DataLoader` para los conjuntos de entrenamiento y validación. Esto permite cargar los datos en lotes, optimizando el uso de la memoria y acelerando el entrenamiento.

In [ ]:
transform = transforms.Compose([
    transforms.Resize((256, 256)), # 256, 256
    transforms.ToTensor()
])


batch_size = 32

# Rutas de los datos de entrenamiento y validación
train_pure = './data/DataSet_Zernike_20_Coef/Train'
#train_random = '/kaggle/input/dataset-ojoartificial/Dataset_exp_OjoArtificial_R/Dataset_exp_OjoArtificial_R/Train'

validation_puros = './data/DataSet_Zernike_20_Coef/Validation'
#validation_random = '/kaggle/input/dataset-ojoartificial/Dataset_exp_OjoArtificial_R/Dataset_exp_OjoArtificial_R/Validation'

train_dirs = [train_pure]
validation_dirs = [validation_puros]

# Crear DataLoaders
train_dataset = CombinedDataset(train_dirs, transform=transform)
validation_dataset = CombinedDataset(validation_dirs, transform=transform)

# DataLoader optimizado
train_loader = DataLoader(
    train_dataset,
    batch_size=32,       # o el máximo que soporte tu memoria GPU
    shuffle=True,
    num_workers=2, # Changed from 4 to 2
    pin_memory=True
)

validation_loader = DataLoader(
    validation_dataset,
    batch_size=32,
    shuffle=False,
    num_workers=2, # Changed from 4 to 2
    pin_memory=True
)

## 5. Definición del Modelo: ResNet-18 para Regresión

Aquí se define la arquitectura del modelo de `Deep Learning` que se utilizará para la predicción de los coeficientes de Zernike. Se adapta una arquitectura ResNet-18 pre-entrenada para esta tarea de regresión.

### 5.1 Clase `ResNet18Model`

Esta clase define el modelo, que es una versión modificada de ResNet-18:
- **`resnet18(weights=ResNet18_Weights.DEFAULT)`**: Carga una ResNet-18 pre-entrenada en ImageNet. El pre-entrenamiento ayuda a inicializar la red con pesos que ya han aprendido características útiles de imágenes, lo cual es beneficioso incluso si las imágenes de Hartmann-Shack son diferentes.
- **`self.resnet.conv1 = nn.Conv2d(1, 64, kernel_size=3, stride=1, padding=1, bias=False)`**: Se modifica la primera capa convolucional para aceptar imágenes de un solo canal (escala de grises) en lugar de las tres canales RGB estándar. También se ajusta el `kernel_size`, `stride` y `padding` para adaptarse a las imágenes de entrada.
- **`self.resnet.fc = nn.Linear(self.resnet.fc.in_features, 20)`**: La capa final (`fully connected` o `fc`) se reemplaza para que la salida sea de 20 valores, correspondientes a los 20 coeficientes de Zernike que el modelo debe predecir. La capa original de ResNet-18 está diseñada para clasificar 1000 categorías de ImageNet.

La arquitectura completa del modelo sigue la estructura de ResNet-18, pero con estas adaptaciones específicas para la tarea de regresión en imágenes en escala de grises. La salida son 20 valores que representan los coeficientes de Zernike.

In [ ]:
#Definir el modelo ResNet-18
class ResNet18Model(nn.Module):
    def __init__(self):
        super(ResNet18Model, self).__init__()
        self.resnet = resnet18(weights=ResNet18_Weights.DEFAULT)
        self.resnet.conv1 = nn.Conv2d(1, 64, kernel_size=3, stride=1, padding=1, bias=False)
        self.resnet.fc = nn.Linear(self.resnet.fc.in_features, 20)

    def forward(self, x):
        return self.resnet(x)

## 6. Función de Evaluación

Esta función se utiliza para evaluar el rendimiento del modelo en un conjunto de datos (validación o prueba), calculando la pérdida (MSE) y los coeficientes de correlación de Pearson para cada coeficiente de Zernike predicho.

### 6.1 `evaluate_model`

- Calcula la pérdida `MSE` promedio en el conjunto de datos.
- Almacena todas las predicciones y etiquetas verdaderas.
- Calcula el coeficiente de correlación de Pearson para cada uno de los 20 coeficientes de Zernike, comparando las predicciones del modelo con los valores reales.

In [ ]:
# Función para evaluación con cálculo de correlación
def evaluate_model(loader, model):
    total_loss = 0.0
    criterion = nn.MSELoss()
    all_predictions = []
    all_labels = []

    with torch.no_grad():
        for images, labels in loader:
            images, labels = images.to(device), labels.to(device)
            outputs = model(images)
            loss = criterion(outputs, labels)
            total_loss += loss.item()
            all_predictions.append(outputs.cpu().numpy())
            all_labels.append(labels.cpu().numpy())


    # Convertir listas en arrays de NumPy
    all_predictions = np.concatenate(all_predictions, axis=0)
    all_labels = np.concatenate(all_labels, axis=0)

    # Calcular coeficiente de correlación por cada coeficiente de salida (18 valores)
    correlations = []
    for i in range(20):  # Asumiendo 18 coeficientes de salida
        corr, _ = stats.pearsonr(all_predictions[:, i], all_labels[:, i])
        correlations.append(corr)

    return total_loss / len(loader), correlations

## 7. Entrenamiento del Modelo

Esta sección configura el dispositivo (GPU si está disponible), instancia el modelo, define la función de pérdida (`MSELoss`) y el optimizador (`Adam`), y ejecuta el bucle de entrenamiento para un número especificado de épocas. También implementa un mecanismo para guardar el mejor modelo basado en la pérdida de validación.

### 7.1 Proceso de Entrenamiento

- **`device`**: Determina si se usará CUDA (GPU) o CPU para el entrenamiento.
- **`model`**: Instancia de `ResNet18Model` movida al dispositivo.
- **`criterion`**: `nn.MSELoss()` para calcular la pérdida entre las predicciones y los coeficientes reales.
- **`optimizer`**: `optim.Adam()` para ajustar los pesos del modelo durante el entrenamiento.
- **Bucle de Épocas**: Itera sobre los datos de entrenamiento, realiza el `forward pass`, calcula la pérdida, el `backward pass` y actualiza los pesos.
- **Pérdidas y Correlaciones**: Se registran las pérdidas de entrenamiento y validación, y se calcula la correlación de los coeficientes en cada época.
- **Guardar Mejor Modelo**: El modelo se guarda si su pérdida de validación es menor que la mejor pérdida de validación registrada hasta el momento.

In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

model = ResNet18Model().to(device)
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

# Entrenamiento del modelo
epochs = 1

best_val_loss = float('inf')

train_losses = []
val_losses = []

for epoch in range(epochs):
    model.train()
    running_loss = 0.0
    with tqdm(train_loader, unit="batch") as tepoch:
        for images, labels in tepoch:
            tepoch.set_description(f"Epoch {epoch+1}")
            images, labels = images.to(device), labels.to(device)  # Mover datos a la GPU
            optimizer.zero_grad()
            outputs = model(images)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()
            running_loss += loss.item()
            tepoch.set_postfix(loss=loss.item())

    # Calcular pérdidas promedio en entrenamiento y validación
    train_loss = running_loss / len(train_loader)
    val_loss, correlations = evaluate_model(validation_loader, model)


    train_losses.append(train_loss)
    val_losses.append(val_loss)

    print(f"Época [{epoch+1}/{epochs}], Pérdida de entrenamiento: {train_loss:.4f}, Pérdida de validación: {val_loss:.4f}")

    # Guardar el mejor modelo basado en validación
    if val_loss < best_val_loss:
        best_val_loss = val_loss
        torch.save(model.state_dict(), "best_resnet18_model_2_replicate.pth")
        print("Modelo guardado con menor pérdida de validación.")


"""
Arquitectura Completa del Modelo:
El modelo completo sigue la estructura de ResNet-18, pero con adaptaciones específicas para trabajar con imágenes en escala de grises y para tener una salida personalizada de 18 valores. La secuencia de operaciones sería la siguiente:

Entrada: Imagen en escala de grises con forma [batch_size, 1, 256, 256].
Capa Inicial: Convolución 7x7, 64 filtros, stride 2 → BatchNorm → ReLU → MaxPooling 3x3.
Bloques Residuales:
Stage 1: 2 bloques con 64 filtros.
Stage 2: 2 bloques con 128 filtros (stride 2 en el primer bloque).
Stage 3: 2 bloques con 256 filtros (stride 2 en el primer bloque).
Stage 4: 2 bloques con 512 filtros (stride 2 en el primer bloque).
Global Average Pooling: Reduce las dimensiones espaciales a 1x1.
Capa Completamente Conectada: Capa fc que da una salida de 18 valores.

Resumen de las Adaptaciones:
Capa Inicial: Modificada para aceptar imágenes en escala de grises.
Bloques Residuales: Implementados como en ResNet-18 estándar, con "skip connections".
Capa de Salida: Modificada para tener 18 salidas en lugar de las 1000 de la versión original (usada en ImageNet).
Este modelo está diseñado para una tarea de regresión, donde la salida es un conjunto de 18 coeficientes,
y se adapta a imágenes en escala de grises, lo cual es un cambio clave respecto a la arquitectura original de ResNet-18.
"""

Epoch 1: 100%|██████████| 850/850 [05:44<00:00,  2.47batch/s, loss=0.081]


Época [1/1], Pérdida de entrenamiento: 0.3092, Pérdida de validación: 0.1175
Modelo guardado con menor pérdida de validación.


'\nArquitectura Completa del Modelo:\nEl modelo completo sigue la estructura de ResNet-18, pero con adaptaciones específicas para trabajar con imágenes en escala de grises y para tener una salida personalizada de 18 valores. La secuencia de operaciones sería la siguiente:\n\nEntrada: Imagen en escala de grises con forma [batch_size, 1, 256, 256].\nCapa Inicial: Convolución 7x7, 64 filtros, stride 2 → BatchNorm → ReLU → MaxPooling 3x3.\nBloques Residuales:\nStage 1: 2 bloques con 64 filtros.\nStage 2: 2 bloques con 128 filtros (stride 2 en el primer bloque).\nStage 3: 2 bloques con 256 filtros (stride 2 en el primer bloque).\nStage 4: 2 bloques con 512 filtros (stride 2 en el primer bloque).\nGlobal Average Pooling: Reduce las dimensiones espaciales a 1x1.\nCapa Completamente Conectada: Capa fc que da una salida de 18 valores.\n\nResumen de las Adaptaciones:\nCapa Inicial: Modificada para aceptar imágenes en escala de grises.\nBloques Residuales: Implementados como en ResNet-18 estándar

## 8. Funciones para Visualización Interactiva

Estas funciones utilizan Plotly para generar gráficos interactivos que muestran la evolución de la pérdida durante el entrenamiento y la correlación de Pearson para cada coeficiente de Zernike.

### 8.1 `plot_loss_interactive`

Crea un gráfico de líneas que muestra la pérdida de entrenamiento y validación a lo largo de las épocas, lo que permite visualizar la convergencia y detectar el sobreajuste.

### 8.2 `plot_correlation_interactive`

Genera un gráfico de barras que muestra el coeficiente de correlación de Pearson para cada uno de los 20 coeficientes de Zernike, lo que indica qué tan bien el modelo predice cada coeficiente.

In [ ]:
# Graficar la pérdida en entrenamiento y validación de forma interactiva
def plot_loss_interactive(epochs, train_losses, val_losses):
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=list(range(epochs)), y=train_losses, mode='lines', name='Entrenamiento'))
    fig.add_trace(go.Scatter(x=list(range(epochs)), y=val_losses, mode='lines', name='Validación', line=dict(dash='dash')))

    fig.update_layout(title='Evolución de la Pérdida durante el Entrenamiento',
                      xaxis_title='Época',
                      yaxis_title='Pérdida',
                      legend_title='Dataset')

    fig.show()
    fig.write_html("Evolutions_loss.html")

# Graficar la correlación de los coeficientes de forma interactiva
def plot_correlation_interactive(correlations):
    indices = list(range(1, len(correlations) + 1))
    fig = px.bar(x=indices, y=correlations, labels={'x': 'Índice del Coeficiente', 'y': 'Coeficiente de Correlación'},
                 title='Correlación entre Predicciones y Valores Reales')
    fig.update_yaxes(range=[-1, 1])
    fig.show()
    fig.write_html("Correlations.html")


## 9. Visualización de Resultados de Validación

Esta sección imprime las pérdidas y las correlaciones obtenidas durante la fase de validación y genera los gráficos interactivos correspondientes.

In [ ]:
# Imprimir resultados
print(f"\nValidation Loss (MSE): {val_loss:.4f}")
print("\nCoeficientes de correlación por coeficiente de salida:")
for i, corr in enumerate(correlations):
    print(f"Coeficiente {i+1}: {corr:.4f}")
print("")


Validation Loss (MSE): 0.1175

Coeficientes de correlación por coeficiente de salida:
Coeficiente 1: 0.9843
Coeficiente 2: 0.9846
Coeficiente 3: 0.9197
Coeficiente 4: 0.9593
Coeficiente 5: 0.9338
Coeficiente 6: 0.9648
Coeficiente 7: 0.9708
Coeficiente 8: 0.9640
Coeficiente 9: 0.9560
Coeficiente 10: 0.9658
Coeficiente 11: 0.9765
Coeficiente 12: 0.9719
Coeficiente 13: 0.9737
Coeficiente 14: 0.9750
Coeficiente 15: 0.9749
Coeficiente 16: 0.9703
Coeficiente 17: 0.9758
Coeficiente 18: 0.9669
Coeficiente 19: 0.9077
Coeficiente 20: 0.8954



In [ ]:
# Grafica interactiva
plot_correlation_interactive(correlations)
plot_loss_interactive(epochs, train_losses, val_losses)

## 10. Evaluación del Modelo en el Conjunto de Test

Esta sección define una función de evaluación más completa para el conjunto de prueba, que calcula métricas adicionales como `RMSE`, `MAE` y `R²`, y genera diagramas de cajas e histogramas interactivos de los errores de predicción.

### 10.1 `evaluate_and_plot_test`

- Calcula `MSE`, `RMSE`, `MAE` y `R²`.
- Genera un diagrama de cajas (`Boxplot`) de los errores para cada coeficiente, mostrando la distribución y los valores atípicos.
- Genera un histograma interactivo de todos los errores de predicción.
- Genera un gráfico de líneas con la frecuencia del error de predicción por coeficiente.
- Exporta estos gráficos a archivos HTML.

In [ ]:
# Función para evaluar el modelo y graficar resultados de forma interactiva
def evaluate_and_plot_test(loader, model, criterion, dataset_name=""):
    model.eval()
    total_loss = 0.0
    all_labels = []
    all_predictions = []

    with torch.no_grad():
        for images, labels in loader:
            images, labels = images.to(device), labels.to(device)
            outputs = model(images)
            loss = criterion(outputs, labels)
            total_loss += loss.item()

            all_labels.append(labels.cpu().numpy())
            all_predictions.append(outputs.cpu().numpy())

    mse_avg_loss = total_loss / len(loader)
    rmse_avg = torch.sqrt(torch.tensor(mse_avg_loss))

    # Convertir listas en arrays para análisis
    all_labels = np.concatenate(all_labels, axis=0)
    all_predictions = np.concatenate(all_predictions, axis=0)

    # Calcular métricas adicionales
    mae = mean_absolute_error(all_labels, all_predictions)
    r2 = r2_score(all_labels, all_predictions)

    # Imprimir métricas
    print(f'[{dataset_name}] Loss (MSE): {mse_avg_loss:.4f}')
    print(f'[{dataset_name}] Loss (RMSE): {rmse_avg:.4f}')
    print(f'[{dataset_name}] MAE: {mae:.4f}')
    print(f'[{dataset_name}] R²: {r2:.4f}')

    # Calcular el error absoluto para cada coeficiente
    errors = all_predictions - all_labels

    df_errors = pd.DataFrame(errors, columns=[f'Coef {i+1}' for i in range(errors.shape[1])])
    df_melted = df_errors.melt(var_name='Coeficiente', value_name='Error')

    fig = px.box(df_melted, x='Coeficiente', y='Error', color='Coeficiente',
                 title='Diagrama de Cajas de Errores por Coeficiente')

    # Crear histograma interactivo de errores

    fig2 = px.histogram(errors, nbins=30, labels={'value': 'Prediction Error'},
                        title=f'{dataset_name}: Histogram of Prediction Errors', opacity=0.7)

    # Crear figura de líneas para errores por coeficiente
    fig3 = go.Figure()

    num_bins = 100  # Puedes ajustar este número según el detalle deseado

    # Crear una línea para cada coeficiente
    for i in range(errors.shape[1]):
        hist, bin_edges = np.histogram(errors[:, i], bins=num_bins)
        bin_centers = 0.5 * (bin_edges[:-1] + bin_edges[1:])

        fig3.add_trace(go.Scatter(
            x=bin_centers,
            y=hist,
            mode='lines',
            name=f'Coef {i+1}'
        ))

    fig3.update_layout(
        title=f'{dataset_name}: Frecuencia del Error de Predicción por Coeficiente',
        xaxis_title='Error de Predicción',
        yaxis_title='Frecuencia',
        template='plotly_white'
    )


    fig.show()
    fig2.show()
    fig3.show()

    fig.write_html("Boxplot.html")
    fig2.write_html("Histogram_Prediction_Errors.html")
    fig3.write_html("Lineplot_Errors_Per_Coefficient.html")

    return rmse_avg, mse_avg_loss, mae, r2, all_predictions, all_labels, errors

### 10.2 Preparación y Evaluación del DataLoader de Test

Se crea el `DataLoader` para el conjunto de prueba y se llama a la función `evaluate_and_plot_test` para obtener y visualizar los resultados del modelo en datos no vistos durante el entrenamiento o la validación.

In [ ]:
# Crear DataLoader para Test y Validation
test_pure = './data/DataSet_Zernike_20_Coef/Test'
#test_random = '/kaggle/input/dataset-ojoartificial/Dataset_exp_OjoArtificial_R/Dataset_exp_OjoArtificial_R/Test'

test_dirs = [test_pure]


test_dataset = CombinedDataset(test_dirs, transform=transform)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)


# Definir criterio de pérdida
criterion = torch.nn.MSELoss()

In [ ]:
# Evaluar en los conjuntos de Test y Validation
test_loss,test_loss_rmse, test_mae, test_r2, all_predictions, all_labels, errors = evaluate_and_plot_test(test_loader, model, criterion, "Test Set")

[Test Set] Loss (MSE): 0.0601
[Test Set] Loss (RMSE): 0.2452
[Test Set] MAE: 0.1708
[Test Set] R²: 0.9163


## 11. Guardar Predicciones y Métricas

Esta sección se encarga de guardar las predicciones del modelo, las etiquetas verdaderas, los errores, y las pérdidas de entrenamiento/validación en archivos CSV para su posterior análisis o uso.

### 11.1 Guardar Datos de Predicción, Etiquetas y Errores

Se convierte la información relevante en DataFrames de Pandas y se guarda en `predictions_Replicate.csv`.

### 11.2 Guardar Pérdidas de Entrenamiento y Validación

Las pérdidas registradas durante el entrenamiento y la validación se guardan en `Train_Val_losses_Replicate.csv`.

In [ ]:
# Asegurar que los datos sean listas planas
all_predictions = np.array(all_predictions).ravel()
all_labels = np.array(all_labels).ravel()
errors = np.array(errors).ravel()

# Crear un DataFrame con los datos
df = pd.DataFrame({
    "Predictions": all_predictions,
    "Labels": all_labels,
    "Errors": errors
})

df1 = pd.DataFrame({
    "Train_losses": train_losses,
    "Val_losses": val_losses
})

# Guardar el DataFrame en un archivo CSV
df.to_csv("predictions_Replicate.csv", index=False, encoding="utf-8")

# Guardar el DataFrame en un archivo CSV
df.to_csv("Train_Val_losses_Replicate.csv", index=False, encoding="utf-8")

print("Datos guardados en predicciones.csv")

Datos guardados en predicciones.csv


### 11.3 Guardar Coeficientes de Correlación

Los coeficientes de correlación de Pearson por cada coeficiente de Zernike se guardan en `Correlations_Replicate.csv`.

In [ ]:
df2 = pd.DataFrame({
    "Correlations": correlations
})

df.to_csv("Correlations_Replicate.csv", index=False, encoding="utf-8")

print("Datos guardados en Correlations_Replicate.csv")

Datos guardados en Correlations_Replicate.csv


## 12. Evaluación del Modelo con Errores Normalizados

Esta sección introduce una función de evaluación similar a la anterior, pero con una normalización específica para los errores de los primeros dos coeficientes (coeficientes 1 y 2) antes de generar los gráficos.

### 12.1 `evaluate_and_plot_test_norm`

- Realiza los mismos cálculos de métricas y generación de gráficos que `evaluate_and_plot_test`.
- **Normalización**: Los errores de los coeficientes 1 y 2 se dividen por `8.38`. Este valor `8.38` presumiblemente corresponde a un rango máximo o valor de normalización para estos coeficientes, lo que permite visualizar sus errores en una escala relativa.
- Los gráficos generados tienen títulos que indican la normalización (`Norm 1 y 2`).

In [ ]:
# Función para evaluar el modelo y graficar resultados de forma interactiva
def evaluate_and_plot_test_norm(loader, model, criterion, dataset_name=""):
    model.eval()
    total_loss = 0.0
    all_labels = []
    all_predictions = []

    with torch.no_grad():
        for images, labels in loader:
            images, labels = images.to(device), labels.to(device)
            outputs = model(images)
            loss = criterion(outputs, labels)
            total_loss += loss.item()

            all_labels.append(labels.cpu().numpy())
            all_predictions.append(outputs.cpu().numpy())

    mse_avg_loss = total_loss / len(loader)
    rmse_avg = torch.sqrt(torch.tensor(mse_avg_loss))

    # Convertir listas en arrays para análisis
    all_labels = np.concatenate(all_labels, axis=0)
    all_predictions = np.concatenate(all_predictions, axis=0)

    # Calcular métricas adicionales
    mae = mean_absolute_error(all_labels, all_predictions)
    r2 = r2_score(all_labels, all_predictions)

    # Imprimir métricas
    print(f'[{dataset_name}] Loss (MSE): {mse_avg_loss:.4f}')
    print(f'[{dataset_name}] Loss (RMSE): {rmse_avg:.4f}')
    print(f'[{dataset_name}] MAE: {mae:.4f}')
    print(f'[{dataset_name}] R²: {r2:.4f}')

    # Calcular el error absoluto para cada coeficiente
    errors = all_predictions - all_labels

    # Normalizar errores para coeficientes 1 y 2 (Min-Max Scaling)
    errors[:, 0] = errors[:, 0]  / 8.38
    errors[:, 1] = errors[:, 1]  / 8.38


    df_errors = pd.DataFrame(errors, columns=[f'Coef {i+1}' for i in range(errors.shape[1])])
    df_melted = df_errors.melt(var_name='Coeficiente', value_name='Error')

    fig = px.box(df_melted, x='Coeficiente', y='Error', color='Coeficiente',
                 title='Diagrama de Cajas de Errores por Coeficiente Norm 1 y 2')

    # Crear histograma interactivo de errores

    fig2 = px.histogram(errors, nbins=30, labels={'value': 'Prediction Error'},
                        title=f'{dataset_name}: Histogram of Prediction Errors Norm 1 y 2', opacity=0.7)

    # Crear figura de líneas para errores por coeficiente
    fig3 = go.Figure()

    num_bins = 100  # Puedes ajustar este número según el detalle deseado

    # Crear una línea para cada coeficiente
    for i in range(errors.shape[1]):
        hist, bin_edges = np.histogram(errors[:, i], bins=num_bins)
        bin_centers = 0.5 * (bin_edges[:-1] + bin_edges[1:])

        fig3.add_trace(go.Scatter(
            x=bin_centers,
            y=hist,
            mode='lines',
            name=f'Coef {i+1}'
        ))

    fig3.update_layout(
        title=f'{dataset_name}: Frecuencia del Error de Predicción por Coeficiente Norm 1 y 2',
        xaxis_title='Error de Predicción',
        yaxis_title='Frecuencia',
        template='plotly_white'
    )


    fig.show()
    fig2.show()
    fig3.show()

    fig.write_html("Boxplot_Norm_1_2.html")
    fig2.write_html("Histogram_Prediction_Errors_norm_1_2.html")
    fig3.write_html("Lineplot_Errors_Per_Coefficient_norm_1_2.html")

    return rmse_avg, mse_avg_loss, mae, r2, all_predictions, all_labels, errors

### 12.2 Evaluación del DataLoader de Test con Normalización

Se llama a la función `evaluate_and_plot_test_norm` para visualizar los errores de predicción con la normalización aplicada a los coeficientes 1 y 2.

In [ ]:
# Evaluar en los conjuntos de Test y Validation
test_loss,test_loss_rmse, test_mae, test_r2, all_predictions, all_labels, errors = evaluate_and_plot_test_norm(test_loader, model, criterion, "Test Set")

[Test Set] Loss (MSE): 0.0601
[Test Set] Loss (RMSE): 0.2452
[Test Set] MAE: 0.1708
[Test Set] R²: 0.9163
